## Creating bronze and Gold layers

In [0]:
%sql
CREATE DATABASE db_Bronze;
CREATE DATABASE db_Gold;

## Initial Delta loads from csv (DBFS)

In [0]:
riders = spark.read.format("csv").option("inferSchema", "false").option("header", "false").schema("rider_id string, first string, last string, address string, birthday string, account_start_date string, account_end_date string, is_member string").option("sep", ",").load("/FileStore/AzureDbrProject/riders.csv")

payments = spark.read.format("csv").option("inferSchema", "false").option("header", "false").schema("payment_id string, date string, amount string, rider_id string").option("sep", ",").load("/FileStore/AzureDbrProject/payments.csv")

stations = spark.read.format("csv").option("inferSchema", "false").option("header", "false").schema("station_id string, name string, latitude string, longitude string").option("sep", ",").load("/FileStore/AzureDbrProject/stations.csv")

trips = spark.read.format("csv").option("inferSchema", "false").option("header", "false").schema("trip_id string, rideable_type string, started_at  string, ended_at string, start_station_id string, end_station_id string, rider_id string").option("sep", ",").load("/FileStore/AzureDbrProject/trips.csv")

In [0]:
riders.write.format("delta").mode("overwrite").saveAsTable("db_Bronze.stage_Riders")
payments.write.format("delta").mode("overwrite").saveAsTable("db_Bronze.stage_Payments")
stations.write.format("delta").mode("overwrite").saveAsTable("db_Bronze.stage_Stations")
trips.write.format("delta").mode("overwrite").saveAsTable("db_Bronze.stage_Trips")

## (STAR Schema) Create Scripts

In [0]:
%sql
DROP TABLE IF EXISTS db_Gold.fact_time_spent;
DROP TABLE IF EXISTS db_Gold.fact_amount_Spent;
DROP TABLE IF EXISTS db_Gold.time_dimension;
DROP TABLE IF EXISTS db_Gold.station_dimension;
DROP TABLE IF EXISTS db_Gold.rider_dimension;


-- Dimension Tables

CREATE TABLE db_Gold.time_dimension (
    ride_date DATE,
    year_of_date INTEGER,
	quarter_of_year INTEGER,
	month_of_date INTEGER,
	day_of_week VARCHAR(15)
);


CREATE TABLE db_Gold.station_dimension (
    station_id VARCHAR(50),
    station_name VARCHAR(75),
    latitude DECIMAL(10,7),
    longitude DECIMAL(10,7)
);

CREATE TABLE db_Gold.rider_dimension (
    rider_id INTEGER,	
	account_start_date DATE,
    account_end_date DATE,
    age_at_ride_time INTEGER,
    is_member BOOLEAN
);


-- Fact Table

CREATE TABLE db_Gold.fact_time_spent (
    ride_id INTEGER,
	trip_id VARCHAR(50),
    rider_id INTEGER,
    start_station_id VARCHAR(50),
    end_station_id VARCHAR(50),
	rideable_type VARCHAR(75),
    duration_minutes INTEGER,
	start_at_timestamp TIMESTAMP,
    ride_date DATE
);


CREATE TABLE db_Gold.fact_amount_Spent (
	pay_ride_id INTEGER,
    payment_id INTEGER,
    rider_id INTEGER,
	payment_date DATE,
    amount DECIMAL(10,7)
);

## (Star Schema) Insert Scripts

In [0]:
%sql
INSERT INTO db_Gold.rider_dimension (rider_id, account_start_date, account_end_date, is_member, age_at_ride_time)
SELECT DISTINCT
    CAST(rider_id as INT),
    CAST(account_start_date AS DATE),
    CAST(account_end_date AS DATE),
    CAST(is_member AS BOOLEAN),
    COALESCE(YEAR(CAST(account_start_date AS DATE)),0) - COALESCE(YEAR(CAST(birthday AS DATE)),0) AS age_at_ride_time
FROM db_Bronze.stage_riders;

-- Load data into station_dimension
INSERT INTO db_Gold.station_dimension (station_id, station_name, latitude, longitude)
SELECT DISTINCT
    station_id,
    name AS station_name,
    CAST(latitude as DECIMAL(10,7)) as latitude,
    CAST(longitude as DECIMAL(10,7)) as longitude
FROM db_Bronze.stage_stations;

-- Load data into time_dimension
INSERT INTO db_Gold.time_dimension (ride_date, year_of_date, quarter_of_year, month_of_date, day_of_week)
SELECT DISTINCT
   DATE(started_at) AS ride_date,
	YEAR(started_at) AS year_of_date,
	QUARTER(started_at) AS quarter_of_year,
	MONTH(started_at) AS month_of_date,
  date_format(started_at, 'EEEE') AS day_of_week
FROM db_Bronze.stage_trips;

-- Load data into ride_fact
INSERT INTO db_Gold.fact_time_spent (ride_id, trip_id, rider_id, start_station_id, end_station_id, rideable_type, duration_minutes, start_at_timestamp, ride_date)
SELECT
  row_number() OVER (order by 1) as ride_id,
  CAST(t.trip_id as VARCHAR(50)) as trip_id,
  CAST(t.rider_id as INT) as rider_id,
  t.start_station_id,
  t.end_station_id,
  t.rideable_type,
  ROUND(timestampdiff(SECOND, t.ended_at, t.started_at) / 60,2) AS duration_minutes,
  CAST(t.started_at as TIMESTAMP)  AS start_at_timestamp,
  CAST(t.started_at as DATE) AS ride_date
FROM db_Bronze.stage_trips t
JOIN db_Gold.time_dimension td ON DATE(t.started_at) = td.ride_date
JOIN db_Gold.station_dimension ss ON t.start_station_id = ss.station_id
JOIN db_Gold.station_dimension es ON t.end_station_id = es.station_id
JOIN db_Gold.rider_dimension rd ON t.rider_id = rd.rider_id;


-- Load data into payment_dimension
INSERT INTO db_Gold.fact_amount_Spent (pay_ride_id, payment_id, rider_id, payment_date, amount)
SELECT DISTINCT
  ROW_NUMBER() OVER (ORDER BY 1) AS pay_ride_id,
	CAST(p.payment_id as INT) as payment_id,
	r.rider_id,
  CAST(p.date as DATE) as payment_date,
  CAST(p.amount AS DECIMAL(10,7)) as amount
FROM db_Bronze.stage_payments p 
JOIN db_Gold.rider_dimension r
on CAST(p.rider_id AS INT) = r.rider_id;

num_affected_rows num_inserted_rows 1946607 1946607

## Solution 1

In [0]:
%sql
-- a. Based on date and time factors such as day of the week and time of day
SELECT
    day_of_week,
    EXTRACT(HOUR FROM t.start_at_timestamp) AS hour_of_day,
    ROUND(AVG(duration_minutes),2) AS average_duration
FROM db_Gold.fact_time_spent t
JOIN db_Gold.time_dimension td 
ON t.ride_date = td.ride_date
GROUP BY td.day_of_week, hour_of_day
ORDER BY td.day_of_week, hour_of_day;

day_of_week hour_of_day average_duration Friday 0 -23.3 Friday 1 -31.79 Friday 2 -40.52 Friday 3 -27.69 Friday 4 -26.44 Friday 5 -11.12 Friday 6 -11.91 Friday 7 -12.14 Friday 8 -13.45 Friday 9 -16.12 Friday 10 -20.41 Friday 11 -20.81 Friday 12 -21.06 Friday 13 -23.09 Friday 14 -22.72 Friday 15 -21.22 Friday 16 -19.34 Friday 17 -20.35 Friday 18 -19.59 Friday 19 -19.99 Friday 20 -23.07 Friday 21 -22.89 Friday 22 -25.46 Friday 23 -23.99 Monday 0 -37.84 Monday 1 -42.23 Monday 2 -28.51 Monday 3 -40.61 Monday 4 -20.11 Monday 5 -12.09 Monday 6 -12.75 Monday 7 -12.57 Monday 8 -13.48 Monday 9 -16.84 Monday 10 -21.35 Monday 11 -23.5 Monday 12 -22.11 Monday 13 -23.61 Monday 14 -25.52 Monday 15 -21.62 Monday 16 -20.37 Monday 17 -18.72 Monday 18 -18.6 Monday 19 -18.61 Monday 20 -21.3 Monday 21 -21.21 Monday 22 -22.12 Monday 23 -23.13 Saturday 0 -24.91 Saturday 1 -23.89 Saturday 2 -31.63 Saturday 3 -28.63 Saturday 4 -62.67 Saturday 5 -20.06 Saturday 6 -19.71 Saturday 7 -17.44 Saturday 8 -18.72 Saturday 9 -20.91 Saturday 10 -22.88 Saturday 11 -24.89 Saturday 12 -26.41 Saturday 13 -27.16 Saturday 14 -26.98 Saturday 15 -27.19 Saturday 16 -25.57 Saturday 17 -24.05 Saturday 18 -26.91 Saturday 19 -24.8 Saturday 20 -26.28 Saturday 21 -28.82 Saturday 22 -29.28 Saturday 23 -27.84 Sunday 0 -24.65 Sunday 1 -31.86 Sunday 2 -31.44 Sunday 3 -38.41 Sunday 4 -31.23 Sunday 5 -26.18 Sunday 6 -23.33 Sunday 7 -26.28 Sunday 8 -22.75 Sunday 9 -24.26 Sunday 10 -26.89 Sunday 11 -26.84 Sunday 12 -26.29 Sunday 13 -28.0 Sunday 14 -29.08 Sunday 15 -28.32 Sunday 16 -27.68 Sunday 17 -27.89 Sunday 18 -27.11 Sunday 19 -26.22 Sunday 20 -24.92 Sunday 21 -26.57 Sunday 22 -25.6 Sunday 23 -31.62 Thursday 0 -20.88 Thursday 1 -26.03 Thursday 2 -42.6 Thursday 3 -18.24 Thursday 4 -13.51 Thursday 5 -10.64 Thursday 6 -12.06 Thursday 7 -11.63 Thursday 8 -12.11 Thursday 9 -14.32 Thursday 10 -19.32 Thursday 11 -18.82 Thursday 12 -19.24 Thursday 13 -18.44 Thursday 14 -19.51 Thursday 15 -20.59 Thursday 16 -17.11 Thursday 17 -17.03 Thursday 18 -17.95 Thursday 19 -20.14 Thursday 20 -19.41 Thursday 21 -20.61 Thursday 22 -21.0 Thursday 23 -18.76 Tuesday 0 -25.19 Tuesday 1 -27.06 Tuesday 2 -44.44 Tuesday 3 -42.57 Tuesday 4 -20.04 Tuesday 5 -12.85 Tuesday 6 -11.5 Tuesday 7 -12.8 Tuesday 8 -12.89 Tuesday 9 -14.88 Tuesday 10 -19.03 Tuesday 11 -18.59 Tuesday 12 -18.54 Tuesday 13 -20.37 Tuesday 14 -19.61 Tuesday 15 -18.69 Tuesday 16 -18.08 Tuesday 17 -17.5 Tuesday 18 -17.83 Tuesday 19 -18.05 Tuesday 20 -18.55 Tuesday 21 -18.44 Tuesday 22 -20.73 Tuesday 23 -25.76 Wednesday 0 -28.96 Wednesday 1 -33.02 Wednesday 2 -36.56 Wednesday 3 -38.0 Wednesday 4 -12.86 Wednesday 5 -11.39 Wednesday 6 -11.2 Wednesday 7 -12.19 Wednesday 8 -12.89 Wednesday 9 -15.56 Wednesday 10 -18.07 Wednesday 11 -18.46 Wednesday 12 -18.82 Wednesday 13 -19.0 Wednesday 14 -20.28 Wednesday 15 -20.74 Wednesday 16 -17.88 Wednesday 17 -16.99 Wednesday 18 -16.82 Wednesday 19 -18.87 Wednesday 20 -19.26 Wednesday 21 -17.62 Wednesday 22 -17.82 Wednesday 23 -25.09

In [0]:
%sql
--b. Based on which station is the starting and/or ending station
SELECT
    ss.station_name AS start_station,
    es.station_name AS end_station,
    ROUND(AVG(duration_minutes),2) AS average_duration
FROM db_Gold.fact_time_spent t
JOIN db_Gold.station_dimension ss ON t.start_station_id = ss.station_id
JOIN db_Gold.station_dimension es ON t.end_station_id = es.station_id
GROUP BY start_station, end_station
having ss.station_name <> es.station_name
ORDER BY start_station, end_station;

start_station end_station average_duration 2112 W Peterson Ave Ashland Ave & Division St -25.0 2112 W Peterson Ave Ashland Ave & Wrightwood Ave -33.0 2112 W Peterson Ave Broadway & Argyle St -42.83 2112 W Peterson Ave Broadway & Barry Ave -38.0 2112 W Peterson Ave Broadway & Berwyn Ave -17.0 2112 W Peterson Ave Broadway & Granville Ave -15.9 2112 W Peterson Ave Broadway & Ridge Ave -14.39 2112 W Peterson Ave Broadway & Sheridan Rd -98.5 2112 W Peterson Ave Broadway & Thorndale Ave -16.21 2112 W Peterson Ave Broadway & Wilson - Truman College Vaccination Site -27.86 2112 W Peterson Ave Budlong Woods Library -16.88 2112 W Peterson Ave California Ave & Fletcher St -60.5 2112 W Peterson Ave California Ave & Montrose Ave -34.0 2112 W Peterson Ave Campbell Ave & Montrose Ave -32.8 2112 W Peterson Ave Chicago Ave & Sheridan Rd -27.0 2112 W Peterson Ave Christiana Ave & Lawrence Ave -22.0 2112 W Peterson Ave Clarendon Ave & Gordon Ter -25.0 2112 W Peterson Ave Clarendon Ave & Junior Ter -33.0 2112 W Peterson Ave Clarendon Ave & Leland Ave -19.5 2112 W Peterson Ave Clark St & Armitage Ave -43.0 2112 W Peterson Ave Clark St & Berwyn Ave -15.84 2112 W Peterson Ave Clark St & Bryn Mawr Ave -12.96 2112 W Peterson Ave Clark St & Columbia Ave -9.33 2112 W Peterson Ave Clark St & Elmdale Ave -16.04 2112 W Peterson Ave Clark St & Jarvis Ave -37.0 2112 W Peterson Ave Clark St & Leland Ave -15.86 2112 W Peterson Ave Clark St & Lunt Ave -14.61 2112 W Peterson Ave Clark St & Montrose Ave -22.67 2112 W Peterson Ave Clark St & Newport St -21.0 2112 W Peterson Ave Clark St & North Ave -43.0 2112 W Peterson Ave Clark St & Schreiber Ave -11.87 2112 W Peterson Ave Clark St & Touhy Ave -13.0 2112 W Peterson Ave Clark St & Wellington Ave -31.0 2112 W Peterson Ave Clark St & Winnemac Ave -14.1 2112 W Peterson Ave Damen Ave & Clybourn Ave -30.0 2112 W Peterson Ave Damen Ave & Foster Ave -12.89 2112 W Peterson Ave Damen Ave & Leland Ave -21.29 2112 W Peterson Ave Damen Ave & Melrose Ave -21.0 2112 W Peterson Ave Damen Ave & Sunnyside Ave -21.67 2112 W Peterson Ave Drake Ave & Addison St -33.0 2112 W Peterson Ave Francisco Ave & Foster Ave -15.33 2112 W Peterson Ave Franklin St & Jackson Blvd -53.0 2112 W Peterson Ave Glenwood Ave & Morse Ave -28.75 2112 W Peterson Ave Glenwood Ave & Touhy Ave -26.57 2112 W Peterson Ave Greenview Ave & Jarvis Ave -23.0 2112 W Peterson Ave Halsted St & Clybourn Ave -36.0 2112 W Peterson Ave Halsted St & Dickens Ave -43.0 2112 W Peterson Ave Halsted St & Roscoe St -21.83 2112 W Peterson Ave Hoyne Ave & Balmoral Ave -13.17 2112 W Peterson Ave Kedzie Ave & Bryn Mawr Ave -15.17 2112 W Peterson Ave Kedzie Ave & Foster Ave -53.0 2112 W Peterson Ave Kedzie Ave & Leland Ave -26.0 2112 W Peterson Ave Kimball Ave & Belmont Ave -35.0 2112 W Peterson Ave Lake Shore Dr & Belmont Ave -41.0 2112 W Peterson Ave Lake Shore Dr & North Blvd -140.0 2112 W Peterson Ave Lakefront Trail & Bryn Mawr Ave -33.44 2112 W Peterson Ave Lakefront Trail & Wilson Ave -34.0 2112 W Peterson Ave Larrabee St & Armitage Ave -38.2 2112 W Peterson Ave Larrabee St & Webster Ave -33.0 2112 W Peterson Ave Leavitt St & Lawrence Ave -16.6 2112 W Peterson Ave Lincoln Ave & Belle Plaine Ave -18.0 2112 W Peterson Ave Lincoln Ave & Belmont Ave -39.0 2112 W Peterson Ave Lincoln Ave & Fullerton Ave -43.0 2112 W Peterson Ave Lincoln Ave & Peterson Ave -14.0 2112 W Peterson Ave Lincoln Ave & Sunnyside Ave -19.0 2112 W Peterson Ave Lincoln Ave & Winona St -11.0 2112 W Peterson Ave Manor Ave & Leland Ave -23.5 2112 W Peterson Ave Maplewood Ave & Peterson Ave -10.0 2112 W Peterson Ave Marine Dr & Ainslie St -22.07 2112 W Peterson Ave Michigan Ave & Oak St -55.0 2112 W Peterson Ave Monticello Ave & Irving Park Rd -22.5 2112 W Peterson Ave Montrose Harbor -42.0 2112 W Peterson Ave Paulina Ave & North Ave -33.0 2112 W Peterson Ave Racine Ave & Belmont Ave -31.0 2112 W Peterson Ave Racine Ave & Wrightwood Ave -23.0 2112 W Peterson Ave Ravenswood Ave & Lawrence Ave -12.64 2112 W Peterso

In [0]:
%sql
-- c. Based on the age of the rider at the time of the ride
SELECT
    rd.age_at_ride_time,
    AVG(duration_minutes) AS average_duration
FROM db_Gold.fact_time_spent t
JOIN db_Gold.rider_dimension rd ON t.rider_id = rd.rider_id
GROUP BY rd.age_at_ride_time
ORDER BY rd.age_at_ride_time;

age_at_ride_time average_duration 7 -111.0 8 -38.10916784203103 9 -22.380004575611988 10 -19.42817278714142 11 -21.778417361386794 12 -22.94327584077718 13 -22.109441151566468 14 -19.565358160862562 15 -21.03348979766804 16 -20.814120960682068 17 -20.927313183756723 18 -22.039341341456407 19 -21.370271889198943 20 -21.13842867164084 21 -22.128322919302615 22 -22.26010995883058 23 -21.472795390505553 24 -21.079907994191963 25 -20.94691021703653 26 -21.111275129578267 27 -20.785138068250333 28 -22.128583049271768 29 -21.208865760817194 30 -22.022369351417368 31 -21.51523854219931 32 -21.776870214569424 33 -21.712110414123526 34 -20.909262718382596 35 -19.746646975254638 36 -21.106558537255523 37 -22.229745778437557 38 -21.68209739490823 39 -21.603281306580254 40 -21.96498474771216 41 -20.414333280092393 42 -20.70367860986011 43 -20.587485232411293 44 -20.62672714359504 45 -21.691839241535614 46 -20.90415393810599 47 -19.725143274741335 48 -20.24718290431424 49 -22.500125649187467 50 -20.476174718729318 51 -20.668623204923637 52 -21.594848679974245 53 -19.65993203583565 54 -22.482304147465438 55 -20.944103144450732 56 -19.70602001692974 57 -20.313121161362368 58 -21.455516477790805 59 -19.438463525966757 60 -24.012117513730278 61 -17.95270774280173 62 -19.3700042973786 63 -23.134830125920647 64 -24.707582515611062 65 -18.141365811222272 66 -24.145639147802928 67 -21.54066073697586 68 -30.197223828802777 69 -19.498543487307533 70 -16.93833780160858 71 -19.611363636363638 72 -17.67595396729255 73 -17.514204545454547 74 -28.889212827988338

In [0]:
%sql
--d. Based on whether the rider is a member or a casual rider
SELECT
    rd.is_member,
    ROUND(AVG(duration_minutes),2) AS average_duration
FROM db_Gold.fact_time_spent t
JOIN db_Gold.rider_dimension rd ON t.rider_id = rd.rider_id
GROUP BY rd.is_member;

is_member average_duration true -21.41 false -20.83

## Solution 2

In [0]:
%sql
-- 2a. Per month, quarter, year
SELECT
    EXTRACT(YEAR FROM payment_date) AS payment_year,
    EXTRACT(QUARTER FROM payment_date) AS payment_quarter,
    EXTRACT(MONTH FROM payment_date) AS payment_month,
    SUM(amount) AS total_amount
FROM db_Gold.fact_amount_spent
GROUP BY payment_year, payment_quarter, payment_month
ORDER BY payment_year, payment_quarter, payment_month;

payment_year payment_quarter payment_month total_amount 2013 1 2 12.9000000 2013 1 3 817.7500000 2013 2 4 1672.6500000 2013 2 5 2716.7100000 2013 2 6 3775.3000000 2013 3 7 4760.9600000 2013 3 8 5834.3000000 2013 3 9 6672.1000000 2013 4 10 7886.1200000 2013 4 11 9195.4500000 2013 4 12 10349.1000000 2014 1 1 11471.6400000 2014 1 2 12584.9200000 2014 1 3 13385.3600000 2014 2 4 15351.4300000 2014 2 5 16802.1700000 2014 2 6 18110.5400000 2014 3 7 19542.4700000 2014 3 8 20891.4100000 2014 3 9 22526.9300000 2014 4 10 23976.9300000 2014 4 11 25637.6500000 2014 4 12 27121.5000000 2015 1 1 29358.3600000 2015 1 2 30737.8000000 2015 1 3 32937.5400000 2015 2 4 34633.6000000 2015 2 5 36222.0100000 2015 2 6 38474.2400000 2015 3 7 40391.1900000 2015 3 8 42372.8600000 2015 3 9 44319.0000000 2015 4 10 46530.6700000 2015 4 11 49472.9700000 2015 4 12 51782.9800000 2016 1 1 53699.4900000 2016 1 2 56950.9900000 2016 1 3 59070.3200000 2016 2 4 61724.0500000 2016 2 5 64488.0000000 2016 2 6 67136.9900000 2016 3 7 69651.2700000 2016 3 8 73114.1900000 2016 3 9 74731.5600000 2016 4 10 78252.2000000 2016 4 11 81474.8400000 2016 4 12 84826.9100000 2017 1 1 88281.7000000 2017 1 2 91394.2800000 2017 1 3 94633.5000000 2017 2 4 98854.4000000 2017 2 5 101697.0600000 2017 2 6 105314.5100000 2017 3 7 109724.1300000 2017 3 8 114747.0200000 2017 3 9 119356.8400000 2017 4 10 123272.4300000 2017 4 11 128260.0600000 2017 4 12 132836.6100000 2018 1 1 137418.3000000 2018 1 2 142420.5400000 2018 1 3 147189.9700000 2018 2 4 152000.0900000 2018 2 5 158103.3600000 2018 2 6 163802.6400000 2018 3 7 167911.1700000 2018 3 8 175022.6300000 2018 3 9 179484.0100000 2018 4 10 186141.8500000 2018 4 11 191941.4300000 2018 4 12 198669.5100000 2019 1 1 206395.3400000 2019 1 2 213286.7000000 2019 1 3 219597.4100000 2019 2 4 227701.0100000 2019 2 5 234522.3600000 2019 2 6 243091.5000000 2019 3 7 251532.5300000 2019 3 8 258662.8600000 2019 3 9 268256.0900000 2019 4 10 276125.4900000 2019 4 11 285230.1200000 2019 4 12 294257.3800000 2020 1 1 303771.7600000 2020 1 2 313517.5000000 2020 1 3 322366.3700000 2020 2 4 332073.8900000 2020 2 5 341008.2700000 2020 2 6 351315.2100000 2020 3 7 362433.4900000 2020 3 8 374396.5500000 2020 3 9 385576.3400000 2020 4 10 398365.0300000 2020 4 11 409920.4400000 2020 4 12 420704.5500000 2021 1 1 434891.0600000 2021 1 2 447430.3700000 2021 1 3 458784.1700000 2021 2 4 471751.6600000 2021 2 5 485719.2500000 2021 2 6 500206.6500000 2021 3 7 513013.6700000 2021 3 8 527280.7600000 2021 3 9 540993.5300000 2021 4 10 555656.6000000 2021 4 11 566140.6100000 2021 4 12 579229.9200000 2022 1 1 590499.1800000 2022 1 2 599471.2700000

In [0]:
%sql
-- 2b. Per member, based on the age of the rider at account start (Check for the age again)
SELECT
    rd.age_at_ride_time,
    rd.is_member,
    SUM(amount) AS total_amount
FROM db_Gold.fact_amount_spent p
JOIN db_Gold.rider_dimension rd ON p.rider_id = rd.rider_id
GROUP BY rd.age_at_ride_time, rd.is_member
ORDER BY rd.age_at_ride_time, rd.is_member;

age_at_ride_time is_member total_amount 7 true 2142.0000000 8 false 11408.2900000 8 true 28431.0000000 9 false 24345.3100000 9 true 51543.0000000 10 false 41823.6500000 10 true 90774.0000000 11 false 59727.6100000 11 true 151308.0000000 12 false 73015.3900000 12 true 189729.0000000 13 false 105733.7700000 13 true 273312.0000000 14 false 136180.0600000 14 true 312822.0000000 15 false 146238.8600000 15 true 409167.0000000 16 false 174968.1700000 16 true 419292.0000000 17 false 155894.7900000 17 true 412011.0000000 18 false 174152.1600000 18 true 434196.0000000 19 false 163930.3700000 19 true 476793.0000000 20 false 186185.9800000 20 true 452196.0000000 21 false 177002.8000000 21 true 487602.0000000 22 false 181537.4600000 22 true 481707.0000000 23 false 179176.9800000 23 true 469314.0000000 24 false 181145.7800000 24 true 459360.0000000 25 false 176682.3100000 25 true 467838.0000000 26 false 192630.8400000 26 true 479358.0000000 27 false 200261.4600000 27 true 465210.0000000 28 false 173438.8600000 28 true 471105.0000000 29 false 173855.4000000 29 true 433134.0000000 30 false 158272.5100000 30 true 421875.0000000 31 false 147341.6100000 31 true 416682.0000000 32 false 146353.5900000 32 true 412587.0000000 33 false 157747.8000000 33 true 398574.0000000 34 false 149831.7200000 34 true 398916.0000000 35 false 162434.4000000 35 true 359676.0000000 36 false 109715.9700000 36 true 324972.0000000 37 false 109749.1600000 37 true 305055.0000000 38 false 116626.2300000 38 true 280935.0000000 39 false 112943.4600000 39 true 284481.0000000 40 false 86544.6600000 40 true 253386.0000000 41 false 85764.7900000 41 true 234981.0000000 42 false 84382.4200000 42 true 217566.0000000 43 false 86059.8600000 43 true 187902.0000000 44 false 72337.8500000 44 true 188784.0000000 45 false 55847.3500000 45 true 157689.0000000 46 false 67342.5500000 46 true 160128.0000000 47 false 50018.6300000 47 true 144981.0000000 48 false 46063.5800000 48 true 131769.0000000 49 false 44679.2700000 49 true 115668.0000000 50 false 37693.5000000 50 true 92880.0000000 51 false 29872.3700000 51 true 83925.0000000 52 false 31160.0600000 52 true 81099.0000000 53 false 25398.9600000 53 true 67941.0000000 54 false 22789.7700000 54 true 66105.0000000 55 false 19158.8300000 55 true 53307.0000000 56 false 16064.3700000 56 true 50913.0000000 57 false 15652.7200000 57 true 41625.0000000 58 false 9972.2200000 58 true 29133.0000000 59 false 8929.5600000 59 true 30213.0000000 60 false 8388.3300000 60 true 26604.0000000 61 false 6523.4300000 61 true 18792.0000000 62 false 6002.9300000 62 true 12789.0000000 63 false 9069.3200000 63 true 13428.0000000 64 false 6343.6600000 64 true 11466.0000000 65 false 6840.7300000 65 true 9621.0000000 66 false 6862.2500000 66 true 5931.0000000 67 false 3867.7000000 67 true 7668.0000000 68 false 2478.2300000 68 true 5031.0000000 69 false 1253.8700000 69 true 5067.0000000 70 false 1416.7100000 70 true 2745.0000000 71 false 351.0000000 71 true 4473.0000000 72 false 800.5800000 72 true 1467.0000000 73 false 1175.3900000 73 true 756.0000000 74 false 895.1700000 74 true 504.0000000 75 false 72.8800000 75 true 243.0000000

## Solution 3

In [0]:
%sql
--3a. Based on how many rides the rider averages per month
SELECT
    rd.rider_id,
    COUNT(*) AS total_rides,
    ROUND(AVG(amount),2) AS average_amount
FROM db_Gold.fact_amount_spent p
JOIN db_Gold.rider_dimension rd ON p.rider_id = rd.rider_id
JOIN db_Gold.fact_time_spent t ON rd.rider_id = t.rider_id
GROUP BY rd.rider_id
ORDER BY total_rides DESC;

rider_id total_rides average_amount 71138 133200 9.00 3897 128775 9.00 52113 125178 9.00 27866 110000 9.00 36271 107001 12.98 7667 95880 9.00 21973 92220 14.81 4193 91589 9.00 36662 90780 9.00 37388 90288 9.00 7126 87472 9.00 32449 85070 9.00 39694 84280 9.00 41323 84224 13.90 66871 82650 9.00 31759 75960 9.00 4083 75831 9.00 3564 75264 14.10 42479 74324 9.00 8578 73800 9.00 6048 73315 14.90 16670 72380 9.00 40666 71820 9.00 53843 71334 9.00 54174 70896 9.00 19270 69422 15.48 17586 69185 9.00 75648 68724 14.03 20599 66780 9.00 30407 65968 9.00 57009 65720 9.00 45984 65442 13.54 36102 63920 9.00 4111 63700 13.58 11815 62424 9.00 20322 61584 9.00 9572 60564 13.80 62636 60260 9.00 72502 59892 9.00 4325 59514 9.00 14481 58855 9.00 40407 58635 9.00 19330 58523 13.07 16853 58183 9.00 45750 57825 15.10 57571 57820 13.00 14624 57820 9.00 55489 57330 9.00 67922 57290 14.38 72094 57200 9.00 52706 57068 9.00 10406 56729 9.00 53395 55620 14.33 63281 55330 9.00 69974 54520 9.00 27563 54038 15.64 32326 53781 9.00 10030 53766 9.00 40911 53704 9.00 7408 53664 9.00 37276 53600 12.49 46756 53250 9.00 39077 53165 9.00 16528 52895 14.93 54162 52886 9.00 16739 52871 9.00 18367 52865 9.00 54601 52416 9.00 35584 52185 9.00 1554 52020 9.00 48832 51730 9.00 75116 51600 9.00 36422 51356 9.00 4021 51332 15.11 5836 51313 14.12 27506 51310 9.00 23460 51205 13.78 62511 50808 9.00 11243 50619 9.00 53651 50440 9.00 18182 50286 9.00 65685 50215 9.00 8654 50058 9.00 46854 49920 9.00 68679 49764 9.00 54889 49404 9.00 41619 49167 9.00 62649 48960 13.45 55165 48818 9.00 68942 48804 12.80 39285 48708 9.00 49397 48490 9.00 60207 48440 9.00 3757 48400 9.00 65989 48312 13.92 46929 48074 13.36 70709 47971 9.00 14676 47718 9.00 27509 47492 12.90 67239 47223 13.53 1088 47096 9.00 25890 47075 15.97 71166 46816 9.00 6003 46575 9.00 3531 46480 9.00 72791 46342 14.32 66471 46248 9.00 53976 46024 9.00 41990 45700 9.00 59628 45540 12.68 20466 45493 9.00 65741 45150 9.00 70450 45100 9.00 18861 45050 9.00 55028 45024 9.00 31311 44982 9.00 28361 44976 9.00 24176 44896 9.00 26736 44604 12.80 49122 44600 9.00 30790 44100 9.00 33317 43882 9.00 65089 43763 15.50 20666 43745 13.56 8857 43632 9.00 62260 43431 9.00 33017 43200 9.00 47715 42945 9.00 24548 42876 9.00 18930 42670 9.00 29775 42000 9.00 51078 42000 9.00 75597 41902 9.00 26819 41810 9.00 3503 41790 9.00 14482 41760 9.00 48824 41745 9.00 62042 41550 9.00 9841 41474 13.88 66277 41391 9.00 55955 41385 9.00 34786 41340 9.00 33666 41184 13.79 28750 40824 13.59 39095 40716 9.00 53733 40698 9.00 54740 40581 9.00 6770 40560 14.06 22928 40426 9.00 26317 40375 9.00 47948 40066 13.41 5184 40064 15.71 46899 39964 9.00 37373 39951 9.00 55926 39886 14.78 61296 39872 9.00 20286 39672 9.00 68008 39672 9.00 73276 39449 13.88 17197 39440 9.00 66940 39421 9.00 72087 39312 9.00 63917 39204 13.78 58665 39066 9.00 53507 39060 9.00 59426 38985 14.42 60263 38808 9.00 27630 38592 13.71 53900 38556 14.55 65552 38544 9.00 3876 38425 9.00 7624 38400 9.00 41742 38270 9.00 7277 38213 9.00 33721 38164 9.00 73848 38136 14.31 30151 38092 9.00 53625 38052 9.00 48969 37920 9.00 54717 37760 14.33 47686 37740 9.00 46494 37654 9.00 53813 37584 9.00 57846 37582 9.00 30454 37526 15.04 31007 37440 9.00 53641 37440 9.00 35755 37350 9.00 47029 37320 11.87 26483 37318 9.00 25862 37310 9.00 20993 37238 9.00 21526 37206 12.98 72899 37130 9.00 64452 37076 9.00 56589 36975 9.00 21759 36912 14.50 7778 36865 9.00 6969 36855 9.00 75765 36800 9.00 40921 36784 9.00 46207 36720 9.00 29465 36480 9.00 21434 36400 9.00 53899 36372 13.05 66814 36348 9.00 57925 36348 9.00 44401 36330 9.00 24798 36328 9.00 16270 36294 9.00 71424 36281 9.00 60815 36271 9.00 3780 36270 9.00 22817 36195 9.00 38367 36180 9.00 53294 36084 9.00 52428 35986 9.00 34940 35948 12.73 15638 35940 9.00 42353 35880 9.00 38423 35757 9.00 67274 35684 9.00 13747 35554 9.00 53421 35518 14.84 43761 35460 9.00 49566 35435 9.00 20074 35340 9.00 24801 35308 9.00 36272 35298 9.00 11571 35288 9.00 73665 35250 9.00 61508 352

In [0]:
%sql
--3b. Based on how many minutes the rider spends on a bike per month
SELECT
    rd.rider_id,
    EXTRACT(MONTH FROM t.ride_date) AS ride_month,
    SUM(duration_minutes) AS total_duration,
    ROUND(AVG(amount),2) AS average_amount
FROM db_Gold.fact_time_spent t
JOIN db_Gold.rider_dimension rd ON t.rider_id = rd.rider_id
JOIN db_Gold.fact_amount_spent p ON t.rider_id = p.rider_id
GROUP BY rd.rider_id, ride_month
ORDER BY rd.rider_id, ride_month;

rider_id ride_month total_duration average_amount 1000 4 -1088 9.00 1000 5 -1496 9.00 1000 6 -306 9.00 1000 7 -2210 9.00 1000 8 -2176 9.00 1000 9 -2346 9.00 1000 10 -578 9.00 1000 11 -1870 9.00 1003 1 -750 13.70 1003 2 -750 13.70 1003 3 -1920 13.70 1003 4 -7500 13.70 1003 5 -4770 13.70 1003 6 -8580 13.70 1003 7 -12270 13.70 1003 8 -6240 13.70 1003 9 -6960 13.70 1003 10 -5550 13.70 1003 11 -1980 13.70 1003 12 -1320 13.70 1006 1 -182 9.00 1006 3 -1469 9.00 1006 4 -1911 9.00 1006 5 -4134 9.00 1006 6 -4498 9.00 1006 7 -7033 9.00 1006 8 -6331 9.00 1006 9 -3536 9.00 1006 10 -1339 9.00 1006 11 -1729 9.00 1006 12 -1027 9.00 1007 1 -1736 13.61 1007 3 -12276 13.61 1007 4 -8308 13.61 1007 5 -16058 13.61 1007 6 -15996 13.61 1007 7 -29884 13.61 1007 8 -20026 13.61 1007 9 -26474 13.61 1007 10 -14818 13.61 1007 11 -8494 13.61 1007 12 -6014 13.61 1008 1 -268 9.00 1008 3 -500 9.00 1008 4 -844 9.00 1008 5 -2200 9.00 1008 6 -2284 9.00 1008 7 -2712 9.00 1008 8 -2436 9.00 1008 9 -2056 9.00 1008 10 -2312 9.00 1008 11 -688 9.00 1008 12 -372 9.00 1010 1 -3822 9.00 1010 2 -2080 9.00 1010 3 -5044 9.00 1010 4 -9828 9.00 1010 5 -19552 9.00 1010 6 -9282 9.00 1010 7 -11076 9.00 1010 8 -10504 9.00 1010 9 -14794 9.00 1010 10 -24882 9.00 1010 11 -11674 9.00 1010 12 -4966 9.00 1012 1 -60 9.00 1012 2 -92 9.00 1012 3 -616 9.00 1012 4 -500 9.00 1012 5 -136 9.00 1012 6 -684 9.00 1012 7 -2620 9.00 1012 8 -1244 9.00 1012 9 -1008 9.00 1012 10 -756 9.00 1012 11 -64 9.00 1012 12 -272 9.00 1013 1 -726 9.00 1013 2 -176 9.00 1013 3 -2750 9.00 1013 4 -4147 9.00 1013 5 -4169 9.00 1013 6 -9295 9.00 1013 7 -17061 9.00 1013 8 -15345 9.00 1013 9 -9526 9.00 1013 10 -5368 9.00 1013 11 -3982 9.00 1013 12 -1925 9.00 1014 8 -459 9.00 1015 3 -2475 9.00 1015 4 -2530 9.00 1015 8 -7205 9.00 1015 9 -2090 9.00 1015 12 -3025 9.00 1017 10 -245 9.00 1018 1 -994 17.68 1018 2 -553 17.68 1018 3 -4578 17.68 1018 4 -3045 17.68 1018 5 -9303 17.68 1018 6 -11396 17.68 1018 7 -17171 17.68 1018 8 -9786 17.68 1018 9 -9702 17.68 1018 10 -8554 17.68 1018 11 -1687 17.68 1018 12 -1995 17.68 1020 3 -800 9.00 1020 4 -100 9.00 1020 6 -700 9.00 1020 7 -625 9.00 1020 8 -1100 9.00 1020 9 -425 9.00 1020 10 -25 9.00 1020 11 -75 9.00 1020 12 -50 9.00 1021 1 -1274 13.45 1021 2 -364 13.45 1021 3 -3510 13.45 1021 4 -1820 13.45 1021 5 -4862 13.45 1021 6 -4030 13.45 1021 7 -5018 13.45 1021 8 -5122 13.45 1021 9 -3536 13.45 1021 10 -3146 13.45 1021 11 -1664 13.45 1021 12 -1456 13.45 1024 1 -308 9.00 1024 3 -209 9.00 1024 4 -693 9.00 1024 5 -1716 9.00 1024 6 -2145 9.00 1024 7 -2233 9.00 1024 8 -1903 9.00 1024 9 -1826 9.00 1024 10 -429 9.00 1024 11 -572 9.00 1024 12 -242 9.00 1026 1 -21 9.00 1026 2 -78 9.00 1026 3 -1692 9.00 1026 4 -1434 9.00 1026 5 -4662 9.00 1026 6 -7230 9.00 1026 7 -4470 9.00 1026 8 -6441 9.00 1026 9 -3792 9.00 1026 10 -1584 9.00 1026 11 -495 9.00 1026 12 -213 9.00 1029 1 -30 10.28 1029 3 -110 10.28 1029 4 -240 10.28 1029 5 -380 10.28 1029 6 -360 10.28 1029 7 -690 10.28 1029 8 -630 10.28 1029 9 -1070 10.28 1029 10 -340 10.28 1029 11 -110 10.28 1029 12 -210 10.28 1044 1 -84 9.00 1044 2 -168 9.00 1044 3 -4242 9.00 1044 4 -3927 9.00 1044 5 -11333 9.00 1044 6 -21805 9.00 1044 7 -23646 9.00 1044 8 -16723 9.00 1044 9 -13524 9.00 1044 10 -8197 9.00 1044 11 -1890 9.00 1044 12 -378 9.00 1045 1 -2208 9.00 1045 2 -2990 9.00 1045 3 -3473 9.00 1045 4 -11109 9.00 1045 5 -20723 9.00 1045 6 -21827 9.00 1045 7 -19251 9.00 1045 8 -26036 9.00 1045 9 -18906 9.00 1045 10 -13478 9.00 1045 11 -2783 9.00 1045 12 -3128 9.00 1046 4 -950 9.00 1046 6 -2014 9.00 1046 8 -228 9.00 1046 10 -931 9.00 1046 11 -1653 9.00 1047 1 -8 9.00 1047 3 -80 9.00 1047 4 -93 9.00 1047 5 -245 9.00 1047 6 -294 9.00 1047 7 -511 9.00 1047 8 -36 9.00 1047 9 -153 9.00 1047 10 -59 9.00 1047 11 -35 9.00 1047 12 -12 9.00 1048 1 -816 9.00 1048 2 -238 9.00 1048 3 -3111 9.00 1048 4 -1462 9.00 1048 5 -4896 9.00 1048 6 -5168 9.00 1048 7 -7225 9.00 1048 8 -6375 9.00 1048 9 -4896 9.00 1048 10 -5644 9.00 1048 11 -2227 9.00 1048 12 -1411 9.00 1049 1 -230 9.00 1049 3 -3